In [1]:
import pandas as pd
import numpy as np
from string import digits
from collections import defaultdict,OrderedDict
import re
import math

In [2]:
df = pd.read_csv("hw1_csv.csv",",")

In [3]:
content = df['內容'].str.replace('\d+', '')
content=content.str.replace("[A-Za-z0-9\s+\.\!\/_,$%^*(+\"\']+|[+——！，。？、~@#￥%……&*（）「」;]+", "")
content[76475]=[]

In [4]:
sum(content.str.contains("銀行") == np.nan)

0

# Count all tf-idf

In [5]:
def run_category_n_gram(category,content):
    category_all_dic = defaultdict(dict)
    for i in range(2,7):
        print("gram:",i)
        temp_category = get_tf_idf(i,category,content)
        temp_category = dict(filter(lambda x: x[1]['tf'] > 10, temp_category.items()))
        category_all_dic.update(temp_category)
    return (category_all_dic)

def get_tf_idf(gram,topic,content):
    if topic != "all":
        content = content[content.str.contains(topic,na=False)]
    all_table = defaultdict(dict)
    # all_content_table = defaultdict(dict)
    for data in content:
            content_table = set()
            for i in range(0,len(data)-gram+1):
                temp_word = data[i:i+gram]
                if temp_word not in all_table:
                    all_table[temp_word]["tf"]=1
                    all_table[temp_word]["df"]=1
                    content_table.add(temp_word)
        #             content_table[temp_word]=1
                else:
                    if temp_word not in content_table:
                        all_table[temp_word]["df"]+=1
                    all_table[temp_word]["tf"]+=1
    
        #     all_content_table[count]=content_table 
    return all_table

def count_tf_idf(tf,df,total_df):
    return (1+math.log10(tf))*math.log10(total_df/df)

def count_tf_exp(total_tf,topic_count,total_count):
    return (total_tf*(topic_count/total_count))

def count_df_exp(total_df,topic_count,total_count):
    return (total_df*(topic_count/total_count))

def count_chi_square(f,exp):
    t=f-exp
    if t>0:
        return ((t**2)/exp)
    else:
        return ((-t**2)/exp)

def count_MI(topic_df,topic_count,total_df):
    return (math.log10(topic_df/(topic_count*total_df)))

def count_Lift(topic_df,topic_count,total_df,total_count):
    return ((topic_df/topic_count)/(total_df/total_count))

def count_tags(content,category,bank_2_gram,all_2_gram): 
    total_count = len(content)
    topic_count = len(content[content.str.contains(category,na=False)])
    for words in list(bank_2_gram.keys()):
        if words in all_2_gram:
            topic_tf = bank_2_gram[words]["tf"]
            topic_df = bank_2_gram[words]["df"]
            total_tf = all_2_gram[words]["tf"]
            total_df = all_2_gram[words]["df"]
            if total_tf<=5 or total_df<=5:
                bank_2_gram.pop(words)
                all_2_gram.pop(words)
            else:
                bank_2_gram[words]["tf_idf"]=count_tf_idf(topic_tf,topic_df,total_count)
                bank_2_gram[words]["tf_exp"]=count_tf_exp(total_tf,topic_count,total_count)
                bank_2_gram[words]["df_exp"]=count_df_exp(total_df,topic_count,total_count)
                bank_2_gram[words]["MI"]= count_MI(topic_df,topic_count,total_df)
                bank_2_gram[words]["Lift"]= count_Lift(topic_df,topic_count,total_df,total_count)
                bank_2_gram[words]["df_chi_square"]= count_chi_square(topic_df,bank_2_gram[words]["df_exp"])
                bank_2_gram[words]["tf_chi_square"]= count_chi_square(topic_tf,bank_2_gram[words]["tf_exp"])
                bank_2_gram[words]["tf_idf_MI"]= bank_2_gram[words]["MI"]*bank_2_gram[words]["tf_idf"]
                bank_2_gram[words]["df_tf_chi_square_MI"] = bank_2_gram[words]["MI"]*bank_2_gram[words]["tf_chi_square"]*bank_2_gram[words]["df_chi_square"]
        else:
            del bank_2_gram[words]
    return (bank_2_gram,all_2_gram)

def sort_dict(bank_all_dic, all_2_gram, tag):
    total_count = len(content)
    topic_count = len(content[content.str.contains(category,na=False)])
    print("total_count:",total_count,"topic count:",topic_count)
    ordered_dict = OrderedDict(sorted(bank_all_dic.items(), key=lambda x: x[1][tag], reverse=True))
    ordered_name = list(ordered_dict.keys())[:500]
    ranking_tag = pd.DataFrame(columns=['word','tf','df','tf_idf','total_tf','total_df','tf_chi_square', 'df_chi_square','MI', 'Lift','tf_idf_MI','df_tf_chi_square_MI'])
    for key_word in ordered_name:
        ranking_tag = ranking_tag.append({'word':key_word,'tf':ordered_dict[key_word]['tf'],
                                          'df':ordered_dict[key_word]['df'],
                                          'total_tf':all_2_gram[key_word]['tf'],
                                          'total_df':all_2_gram[key_word]['df'],
                                          'tf_idf':ordered_dict[key_word]['tf_idf'],
                           'tf_chi_square':ordered_dict[key_word]['tf_chi_square'],
                           'df_chi_square':ordered_dict[key_word]['df_chi_square'],
                           'MI':ordered_dict[key_word]['MI'],
                           'Lift':ordered_dict[key_word]['Lift'],
                            'tf_idf_MI':ordered_dict[key_word]['tf_idf_MI'],
                            'df_tf_chi_square_MI':ordered_dict[key_word]['df_tf_chi_square_MI']
                                         },ignore_index = True)
    return (ranking_tag)

def delete_similar_words(ranking_tag):
    words = ranking_tag['word']
    delete_word = list()
    delete_index = list()
    for i in range(0,len(words)-4):
        for j in range(1,5):
            if words[i] in words[i+j] or words[i+j] in words[i]:
#                 print(words[i],words[i+j],"is similar")
                if len(words[i])<len(words[i+j]):
                    delete_word.append(words[i])
                    delete_index.append(i)
                else:
                    delete_word.append(words[i+j])
                    delete_index.append(i+j)
    return (delete_index)

In [ ]:
all_dic = run_category_n_gram("all",content)

In [6]:
import json
with open('all_data.txt') as json_file:  
    all_dic = json.load(json_file)

# Try plotly

In [7]:
# plotly 
import plotly as py
import plotly.graph_objs as go
%load_ext autoreload
%autoreload 2

# offline plot  
# 因為如果寫成func去調用plotly會無法出現，所以只好用offline的方式。
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
from sklearn import preprocessing 

# Create random data with numpy
import numpy as np

In [8]:
def draw_line_plot(ranking_tag):
    random_x = ranking_tag['word']
    random_y0 = preprocessing.scale(ranking_tag['tf_idf'])
    random_y1 = preprocessing.scale(ranking_tag['tf_chi_square'])
    random_y2 = preprocessing.scale(ranking_tag['MI'])
    random_y3 = preprocessing.scale(ranking_tag['Lift'])
    random_y4 = preprocessing.scale(ranking_tag['df_chi_square'])

    # Create traces
    trace0 = go.Scatter(
        x = random_x,
        y = random_y0,
        mode = 'lines+markers',
        name = 'tf_idf'
    )
    trace1 = go.Scatter(
        x = random_x,
        y = random_y1,
        mode = 'lines+markers',
        name = 'tf_chi_square'
    )
    trace2 = go.Scatter(
        x = random_x,
        y = random_y2,
        mode = 'lines+markers',
        name = 'MI'
    )
    trace3 = go.Scatter(
        x = random_x,
        y = random_y3,
        mode = 'lines+markers',
        name = 'Lift'
    )
    trace4 = go.Scatter(
        x = random_x,
        y = random_y4,
        mode = 'lines+markers',
        name = 'df_chi_square'
    )
    data = [trace0, trace1, trace2, trace3, trace4]

    py.offline.iplot(data, filename='line-mode')

In [9]:
def draw_category_tags(category_all_dic,all_dic):
    tags = ['tf_idf','tf_chi_square', 'df_chi_square','MI', 'Lift','tf_idf_MI','df_tf_chi_square_MI']
    for tag in tags:
        print(tag)
        temp_ranking_tag = sort_dict(category_all_dic,all_dic,tag)
        temp_delete_index = delete_similar_words(temp_ranking_tag)
        temp_ranking_tag = temp_ranking_tag.drop(temp_delete_index)
        draw_line_plot(temp_ranking_tag[:150])
    return(temp_ranking_tag)

# 銀行

In [11]:
category = "銀行"
bank_all_dic = run_category_n_gram(category,content)

gram: 2
gram: 3
gram: 4
gram: 5
gram: 6


In [12]:
bank_all_dic,all_dic = count_tags(content,category,bank_all_dic,all_dic)

In [14]:
bank = draw_category_tags(bank_all_dic,all_dic)
bank.to_excel('bank.xlsx', sheet_name='bank', index=False)

tf_idf
total_count: 90507 topic count: 6669


tf_chi_square
total_count: 90507 topic count: 6669


df_chi_square
total_count: 90507 topic count: 6669


MI
total_count: 90507 topic count: 6669


/Users/amandachen/anaconda/envs/py35/lib/python3.5/site-packages/sklearn/preprocessing/data.py:181: UserWarning:

Numerical issues were encountered when scaling the data and might not be solved. The standard deviation of the data is probably very close to 0. 



Lift
total_count: 90507 topic count: 6669


tf_idf_MI
total_count: 90507 topic count: 6669


df_tf_chi_square_MI
total_count: 90507 topic count: 6669


# 信用卡

In [15]:
category = "信用卡"
credit_all_dic = run_category_n_gram(category,content)

gram: 2
gram: 3
gram: 4
gram: 5
gram: 6


In [16]:
credit_all_dic,all_dic = count_tags(content,category,credit_all_dic,all_dic)

In [17]:
credit_card = draw_category_tags(credit_all_dic,all_dic)
credit_card.to_excel('credit_card.xlsx', sheet_name='credit_card', index=False)

tf_idf
total_count: 90507 topic count: 652


tf_chi_square
total_count: 90507 topic count: 652


df_chi_square
total_count: 90507 topic count: 652


MI
total_count: 90507 topic count: 652


/Users/amandachen/anaconda/envs/py35/lib/python3.5/site-packages/sklearn/preprocessing/data.py:181: UserWarning:

Numerical issues were encountered when scaling the data and might not be solved. The standard deviation of the data is probably very close to 0. 



Lift
total_count: 90507 topic count: 652


tf_idf_MI
total_count: 90507 topic count: 652


df_tf_chi_square_MI
total_count: 90507 topic count: 652


# 匯率

In [19]:
category = "匯率"
exchange_all_dic = run_category_n_gram(category,content)
exchange_all_dic,all_dic = count_tags(content,category,exchange_all_dic,all_dic)

gram: 2
gram: 3
gram: 4
gram: 5
gram: 6


In [20]:
exchange_rate = draw_category_tags(exchange_all_dic,all_dic)
exchange_rate.to_excel('exchange_rate.xlsx', sheet_name='exchange_rate', index=False)

tf_idf
total_count: 90507 topic count: 1941


tf_chi_square
total_count: 90507 topic count: 1941


df_chi_square
total_count: 90507 topic count: 1941


MI
total_count: 90507 topic count: 1941


/Users/amandachen/anaconda/envs/py35/lib/python3.5/site-packages/sklearn/preprocessing/data.py:181: UserWarning:

Numerical issues were encountered when scaling the data and might not be solved. The standard deviation of the data is probably very close to 0. 



Lift
total_count: 90507 topic count: 1941


tf_idf_MI
total_count: 90507 topic count: 1941


df_tf_chi_square_MI
total_count: 90507 topic count: 1941


# 台積電

In [21]:
category = "台積電"
tsmc_all_dic = run_category_n_gram(category,content)
tsmc_all_dic,all_dic = count_tags(content,category,tsmc_all_dic,all_dic)

gram: 2
gram: 3
gram: 4
gram: 5
gram: 6


In [23]:
tsmc = draw_category_tags(tsmc_all_dic,all_dic)
tsmc.to_excel('tsmc.xlsx', sheet_name='tsmc', index=False)

tf_idf
total_count: 90507 topic count: 1736


tf_chi_square
total_count: 90507 topic count: 1736


df_chi_square
total_count: 90507 topic count: 1736


MI
total_count: 90507 topic count: 1736


/Users/amandachen/anaconda/envs/py35/lib/python3.5/site-packages/sklearn/preprocessing/data.py:181: UserWarning:

Numerical issues were encountered when scaling the data and might not be solved. The standard deviation of the data is probably very close to 0. 



Lift
total_count: 90507 topic count: 1736


tf_idf_MI
total_count: 90507 topic count: 1736


df_tf_chi_square_MI
total_count: 90507 topic count: 1736


# 台灣

In [24]:
category = "台灣"
taiwan_all_dic = run_category_n_gram(category,content)
taiwan_all_dic,all_dic = count_tags(content,category,taiwan_all_dic,all_dic)

gram: 2
gram: 3
gram: 4
gram: 5
gram: 6


In [25]:
taiwan = draw_category_tags(taiwan_all_dic,all_dic)
taiwan.to_excel('taiwan.xlsx', sheet_name='taiwan', index=False)

tf_idf
total_count: 90507 topic count: 27117


tf_chi_square
total_count: 90507 topic count: 27117


df_chi_square
total_count: 90507 topic count: 27117


MI
total_count: 90507 topic count: 27117


/Users/amandachen/anaconda/envs/py35/lib/python3.5/site-packages/sklearn/preprocessing/data.py:181: UserWarning:

Numerical issues were encountered when scaling the data and might not be solved. The standard deviation of the data is probably very close to 0. 



Lift
total_count: 90507 topic count: 27117


tf_idf_MI
total_count: 90507 topic count: 27117


df_tf_chi_square_MI
total_count: 90507 topic count: 27117


# 日本

In [26]:
category = "日本"
japan_all_dic = run_category_n_gram(category,content)
japan_all_dic,all_dic = count_tags(content,category,japan_all_dic,all_dic)

gram: 2
gram: 3
gram: 4
gram: 5
gram: 6


In [27]:
japan = draw_category_tags(japan_all_dic,all_dic)
japan.to_excel('japan.xlsx', sheet_name='japan', index=False)

tf_idf
total_count: 90507 topic count: 8257


tf_chi_square
total_count: 90507 topic count: 8257


df_chi_square
total_count: 90507 topic count: 8257


MI
total_count: 90507 topic count: 8257


/Users/amandachen/anaconda/envs/py35/lib/python3.5/site-packages/sklearn/preprocessing/data.py:181: UserWarning:

Numerical issues were encountered when scaling the data and might not be solved. The standard deviation of the data is probably very close to 0. 



Lift
total_count: 90507 topic count: 8257


tf_idf_MI
total_count: 90507 topic count: 8257


df_tf_chi_square_MI
total_count: 90507 topic count: 8257
